In [3]:
!pip install plotly_express
!pip install flask

In [3]:
from google.colab import files

In [8]:
files.upload()

Saving NetflixDataset.csv to NetflixDataset.csv


{'NetflixDataset.csv': b'Title,Genre,Tags,Languages,Country Availability,Runtime,Director,Writer,Actors,View Rating,IMDb Score,Awards Received,Awards Nominated For,Boxoffice,Release Date,Netflix Release Date,Production House,Netflix Link,Summary,Series or Movie,IMDb Votes,Image\nLets Fight Ghost,"Crime, Drama, Fantasy, Horror, Romance","Comedy Programmes,Romantic TV Comedies,Horror Programmes,Thai TV Programmes","Swedish, Spanish",Thailand,< 30 minutes,Tomas Alfredson,John Ajvide Lindqvist,"Lina Leandersson, K\xe5re Hedebrant, Per Ragnar, Henrik Dahl",R,7.9,74,57,"$21,22,065",12-Dec-08,04-03-2021,"Canal+, Sandrew Metronome",https://www.netflix.com/watch/81415947,"A med student with a supernatural gift tries to cash in on his abilities by facing off against ghosts, till a wandering spirit brings romance instead.",Series,205926,https://occ-0-4708-64.1.nflxso.net/dnm/api/v6/evlCitJPPCVCry0BZlEFb5-QjKc/AAAABcmgLCxN8dNahdY2kgd1hhcL2a6XrE92x24Bx5h6JFUvH5zMrv6lFWl_aWMt33b6DHvkgsUeDx_8Q1rmopwT

In [1]:
%%writefile app.py

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly_express as px
import seaborn as sns
import math
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from flask import Flask, render_template, request

def create_4train(x):
    return x['Genre'] + ' ' + x['Tags'] + ' ' +x['Actors']+' '+ x['Viewrating']

def find_recommendations(title,cosine_sim2):
  title = title.lower().replace(' ','')
  values = cosine_sim2[title].sort_values(ascending=False)[1:51]
  return values.index.str.title().tolist()

data = pd.read_csv('NetflixDataset.csv',encoding='latin-1',index_col='Title')
data.index = data.index.str.title().str.lower().str.replace(' ','')
data = data[~data.index.duplicated()]

data.rename(columns={'View Rating':'Viewrating'},inplace=True)

new_features = ['Genre', 'Tags', 'Actors', 'Viewrating']
selected_data = data[new_features]
for new_feature in new_features:
  data.loc[:,new_features] = data.loc[:,new_features].apply(lambda x:x.str.replace(' ',''))
  data[new_feature] = data[new_feature].str.lower()

Language = data.Languages.str.get_dummies(',')
Lang = Language.columns.str.strip().values.tolist()
Lang = set(Lang)

Titles = set(data.index.to_list())

data['Genre'] = data['Genre'].fillna('').astype(str)
data['Tags'] = data['Tags'].fillna('').astype(str)
data['Actors'] = data['Actors'].fillna('').astype(str)
data['Viewrating'] = data['Viewrating'].fillna('').astype(str)
score_med = data['IMDb Score'].median()
data['IMDb Score'] = data['IMDb Score'].apply(lambda x:score_med if math.isnan(x) or x==0 else x)

selected_data['Train_fea'] = data.apply(create_4train, axis = 1)

count = CountVectorizer(stop_words='english')
count_matrix = count.fit_transform(selected_data['Train_fea'])
cosine_sim = cosine_similarity(count_matrix, count_matrix)
cosine_sim_df = pd.DataFrame(cosine_sim,columns=data.index,index=data.index)

df = pd.DataFrame()

app = Flask(__name__)

@app.route('/')
def index():
  return render_template('index.html', languages = Lang, titles = Titles)

@app.route('/about',methods=['POST'])
def getvalue():
    global df
    movienames = request.form.getlist('titles')
    languages = request.form.getlist('languages')
    for moviename in movienames:
        get_recommendations(moviename,cosine_sim2)
        for language in languages:
            df = pd.concat([result[result['Languages'].str.count(language) > 0], df], ignore_index=True)
    df.drop_duplicates(keep = 'first', inplace = True)
    df.sort_values(by = 'IMDb Score', ascending = False, inplace = True)
    images = df['Image'].tolist()
    titles = df['Title'].tolist()
    return render_template('result.html',  titles =  titles, images = images)

@app.route('/moviepage/<name>')
def movie_details(name):
    global df
    details_list = df[df['Title'] == name].to_numpy().tolist()
    return render_template('moviepage.html', details = details_list[0])


if __name__ == '__main__':
    app.run(debug=False)

Writing app.py


In [4]:
files.download('app.py')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>